In [1]:
# Libraries
import pandas as pd
import numpy as np
import hvplot.pandas

In [87]:
# Ingest data
df = pd.read_csv("./examples/oj.csv")

#### Data Exploration

In [84]:
df.head()

sales  price      brand  feat
0  8256.0   3.87  tropicana     0
1  6144.0   3.87  tropicana     0
2  3840.0   3.87  tropicana     0
3  8000.0   3.87  tropicana     0
4  8896.0   3.87  tropicana     0

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28947 entries, 0 to 28946
Data columns (total 4 columns):
sales    28947 non-null float64
price    28947 non-null float64
brand    28947 non-null object
feat     28947 non-null int64
dtypes: float64(2), int64(1), object(1)
memory usage: 904.7+ KB


In [5]:
df["brand"].unique()

array(['tropicana', 'minute.maid', 'dominicks'], dtype=object)

In [88]:
df["brand"] = df["brand"].astype("category")
df["log_sales"] = np.log(df["sales"])
df["log_price"] = np.log(df["price"])
df.hvplot.box("log_price", by="brand", color="brand", legend=False).opts(cmap="tab10")

:BoxWhisker   [brand]   (log_price)

In [58]:
df.hvplot.scatter(x="log_price", y="log_sales", color="brand", legend=True).opts(cmap="tab10", alpha=0.2)

:Scatter   [log_price]   (log_sales,brand)

> Dominick’s is the budget option, Tropicana is the luxury option, and Minute Maid lives between.

Taddy, Matt. Business Data Science: Combining Machine Learning and Economics to Optimize, Automate, and Accelerate Business Decisions . McGraw-Hill Education. Kindle Edition. 

#### Why Logarithms?
> Whenever you are working with linear (i.e., additive) models, it is crucial that you try to work in the space where you expect to find linearity. For variables that change multiplicatively with other factors, this is usually the log scale.

Taddy, Matt. Business Data Science: Combining Machine Learning and Economics to Optimize, Automate, and Accelerate Business Decisions . McGraw-Hill Education. Kindle Edition. 

#### Generalized Linear Model No Interaction

In [91]:
# We use use stasmodels and not SK-Learn because the former is developed for inferential statistics; the 
# latter is developed for machine learning prediction. 
import statsmodels.formula.api as smf
# Build the model using the formula api; the C() command treats the brand as a dummy variable automatically. 
smf.glm(formula="log_sales ~ log_price + C(brand)", data=df).fit().summary()


<class 'statsmodels.iolib.summary.Summary'>
"""
                 Generalized Linear Model Regression Results                  
==============================================================================
Dep. Variable:              log_sales   No. Observations:                28947
Model:                            GLM   Df Residuals:                    28943
Model Family:                Gaussian   Df Model:                            3
Link Function:               identity   Scale:                         0.62968
Method:                          IRLS   Log-Likelihood:                -34377.
Date:                Sat, 16 Nov 2019   Deviance:                       18225.
Time:                        16:37:17   Pearson chi2:                 1.82e+04
No. Iterations:                     3                                         
Covariance Type:            nonrobust                                         
===========================================================================================
                              coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------
Intercept                  10.8288      0.015    745.041      0.000      10.800      10.857
C(brand)[T.minute.maid]     0.8702      0.013     67.320      0.000       0.845       0.896
C(brand)[T.tropicana]       1.5299      0.016     93.808      0.000       1.498       1.562
log_price                  -3.1387      0.023   -136.888      0.000      -3.184      -3.094
===========================================================================================
"""

#### Generalized Linear Model, Brand-Price Interaction

In [92]:
# By including this interaction effect we are creating a slope and intercept for each brand; not a single model for all.
smf.glm(formula="log_sales ~ log_price * C(brand)", data=df).fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                 Generalized Linear Model Regression Results                  
==============================================================================
Dep. Variable:              log_sales   No. Observations:                28947
Model:                            GLM   Df Residuals:                    28941
Model Family:                Gaussian   Df Model:                            5
Link Function:               identity   Scale:                         0.62588
Method:                          IRLS   Log-Likelihood:                -34289.
Date:                Sat, 16 Nov 2019   Deviance:                       18114.
Time:                        16:43:28   Pearson chi2:                 1.81e+04
No. Iterations:                     3                                         
Covariance Type:            nonrobust                                         
=====================================================================================================
                                        coef    std err          z      P>|z|      [0.025      0.975]
-----------------------------------------------------------------------------------------------------
Intercept                            10.9547      0.021    529.136      0.000      10.914      10.995
C(brand)[T.minute.maid]               0.8883      0.042     21.376      0.000       0.807       0.970
C(brand)[T.tropicana]                 0.9624      0.046     20.719      0.000       0.871       1.053
log_price                            -3.3775      0.036    -93.322      0.000      -3.448      -3.307
log_price:C(brand)[T.minute.maid]     0.0568      0.057      0.991      0.322      -0.055       0.169
log_price:C(brand)[T.tropicana]       0.6658      0.054     12.439      0.000       0.561       0.771
=====================================================================================================
"""

#### Calculating the Brand Price Elasticities

> The reference category is dominicks; this brand is absorbed into both the intercept and the main slope term on log price. You find the elasticities for the other brands by adding the log(price):brand interaction terms to this main slope.

Taddy, Matt. Business Data Science: Combining Machine Learning and Economics to Optimize, Automate, and Accelerate Business Decisions . McGraw-Hill Education. Kindle Edition. 

In [96]:
# Calculating the elasticities from the price/brand interactions
dom_elas = -3.37
min_elas = -3.37 + 0.0568
trop_elas = -3.37 + 0.6658
print(
    "The elasticity for Dominicks is {}, Minute Maid is {}, and Tropicana is {}. Tropicana customers are less sensitive than the others.".format(
        dom_elas, min_elas, trop_elas
    )
)

The elasticity for Dominicks is -3.37, Minute Maid is -3.3132, and Tropicana is -2.7042. Tropicana customers are less sensitive than the others.


#### Adding the Advertising `feat` Variable as an Interaction

In [99]:
# By including this interaction effect we are creating a slope and intercept for each brand; not a single model for all.
smf.glm(formula="log_sales ~ log_price * C(brand) * feat", data=df).fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                 Generalized Linear Model Regression Results                  
==============================================================================
Dep. Variable:              log_sales   No. Observations:                28947
Model:                            GLM   Df Residuals:                    28935
Model Family:                Gaussian   Df Model:                           11
Link Function:               identity   Scale:                         0.48297
Method:                          IRLS   Log-Likelihood:                -30534.
Date:                Sat, 16 Nov 2019   Deviance:                       13975.
Time:                        16:56:38   Pearson chi2:                 1.40e+04
No. Iterations:                     3                                         
Covariance Type:            nonrobust                                         
==========================================================================================================
                                             coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------------------------------------
Intercept                                 10.4066      0.023    445.668      0.000      10.361      10.452
C(brand)[T.minute.maid]                    0.0472      0.047      1.012      0.311      -0.044       0.139
C(brand)[T.tropicana]                      0.7079      0.051     13.937      0.000       0.608       0.808
log_price                                 -2.7742      0.039    -71.445      0.000      -2.850      -2.698
log_price:C(brand)[T.minute.maid]          0.7829      0.061     12.750      0.000       0.663       0.903
log_price:C(brand)[T.tropicana]            0.7358      0.057     12.946      0.000       0.624       0.847
feat                                       1.0944      0.038     28.721      0.000       1.020       1.169
C(brand)[T.minute.maid]:feat               1.1729      0.082     14.312      0.000       1.012       1.334
C(brand)[T.tropicana]:feat                 0.7853      0.099      7.952      0.000       0.592       0.979
log_price:feat                            -0.4706      0.074     -6.351      0.000      -0.616      -0.325
log_price:C(brand)[T.minute.maid]:feat    -1.1092      0.122     -9.074      0.000      -1.349      -0.870
log_price:C(brand)[T.tropicana]:feat      -0.9861      0.124     -7.946      0.000      -1.229      -0.743
==========================================================================================================
"""

> We see that being featured always leads to more price sensitivity. Minute Maid and Tropicana elasticities drop from −2 to below −3.5 with ads, while Dominick’s drops from −2.8 to −3.2. Why does this happen? One possible explanation is that advertisement increases the population of consumers who are considering your brand.

> There is also an alternative explanation. Since the featured products are often also discounted, it could be that the demand curve is nonlinear—at lower price points the average consumer is more price sensitive. The truth is probably a combination of these effects.

Taddy, Matt. Business Data Science: Combining Machine Learning and Economics to Optimize, Automate, and Accelerate Business Decisions . McGraw-Hill Education. Kindle Edition. 


### Logistic Regression
Logistic regression is a linear model for log-odds.

In [4]:
email = df = pd.read_csv("./examples/spam.csv")

In [5]:
email.head()

word_make  word_address  word_all  word_3d  word_our  word_over  \
0          0             1         1        0         1          0   
1          1             1         1        0         1          1   
2          1             0         1        0         1          1   
3          0             0         0        0         1          0   
4          0             0         0        0         1          0   

   word_remove  word_internet  word_order  word_mail  ...  char_semicolon  \
0            0              0           0          0  ...               0   
1            1              1           0          1  ...               0   
2            1              1           1          1  ...               1   
3            1              1           1          1  ...               0   
4            1              1           1          1  ...               0   

   char_leftbrac  char_leftsquarebrac  char_exclaim  char_dollar  char_pound  \
0              0                    0             1            0           0   
1              1                    0             1            1           1   
2              1                    0             1            1           1   
3              1                    0             1            0           0   
4              1                    0             1            0           0   

   capital_run_length_average  capital_run_length_longest  \
0                       3.756                          61   
1                       5.114                         101   
2                       9.821                         485   
3                       3.537                          40   
4                       3.537                          40   

   capital_run_length_total  spam  
0                       278     1  
1                      1028     1  
2                      2259     1  
3                       191     1  
4                       191     1  

[5 rows x 58 columns]

In [28]:

# Create a string of the oredictive variables to use in the regression formula
# We remove the target variable "spam" from the list.
all_columns = " + ".join(email.columns).replace(" + spam", "")
all_columns


'word_make + word_address + word_all + word_3d + word_our + word_over + word_remove + word_internet + word_order + word_mail + word_receive + word_will + word_people + word_report + word_addresses + word_free + word_business + word_email + word_you + word_credit + word_your + word_font + word_000 + word_money + word_hp + word_hpl + word_george + word_650 + word_lab + word_labs + word_telnet + word_857 + word_data + word_415 + word_85 + word_technology + word_1999 + word_parts + word_pm + word_direct + word_cs + word_meeting + word_original + word_project + word_re + word_edu + word_table + word_conference + char_semicolon + char_leftbrac + char_leftsquarebrac + char_exclaim + char_dollar + char_pound + capital_run_length_average + capital_run_length_longest + capital_run_length_total'

In [33]:
# Logistic regression model
import statsmodels.formula.api as smf
log_model = smf.logit(formula="spam ~" + str(all_columns), data=email).fit()
log_model.summary()

Optimization terminated successfully.
         Current function value: 0.168296
         Iterations 12


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:                   spam   No. Observations:                 4601
Model:                          Logit   Df Residuals:                     4543
Method:                           MLE   Df Model:                           57
Date:                Tue, 19 Nov 2019   Pseudo R-squ.:                  0.7490
Time:                        14:22:33   Log-Likelihood:                -774.33
converged:                       True   LL-Null:                       -3085.1
Covariance Type:            nonrobust   LLR p-value:                     0.000
==============================================================================================
                                 coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------------------------
Intercept                     -1.9682      0.147    -13.429      0.000      -2.256      -1.681
word_make                     -0.5530      0.236     -2.346      0.019      -1.015      -0.091
word_address                  -0.1339      0.222     -0.604      0.546      -0.568       0.301
word_all                      -0.4946      0.178     -2.786      0.005      -0.843      -0.147
word_3d                        0.8302      0.824      1.007      0.314      -0.786       2.446
word_our                       1.1253      0.174      6.471      0.000       0.784       1.466
word_over                      0.2751      0.222      1.238      0.216      -0.160       0.711
word_remove                    2.4881      0.276      9.013      0.000       1.947       3.029
word_internet                  0.9334      0.252      3.702      0.000       0.439       1.428
word_order                     0.2196      0.277      0.793      0.428      -0.323       0.762
word_mail                      0.3081      0.195      1.579      0.114      -0.074       0.691
word_receive                  -0.4392      0.279     -1.576      0.115      -0.985       0.107
word_will                     -0.3106      0.160     -1.943      0.052      -0.624       0.003
word_people                   -0.9586      0.255     -3.765      0.000      -1.458      -0.460
word_report                    0.8467      0.343      2.471      0.013       0.175       1.518
word_addresses                 1.2553      0.558      2.248      0.025       0.161       2.350
word_free                      1.5427      0.179      8.621      0.000       1.192       1.893
word_business                  1.0566      0.250      4.221      0.000       0.566       1.547
word_email                    -0.5201      0.211     -2.462      0.014      -0.934      -0.106
word_you                       0.1628      0.173      0.944      0.345      -0.175       0.501
word_credit                    0.4160      0.409      1.017      0.309      -0.386       1.218
word_your                      0.6950      0.171      4.063      0.000       0.360       1.030
word_font                      1.2999      0.437      2.974      0.003       0.443       2.157
word_000                       1.0350      0.309      3.348      0.001       0.429       1.641
word_money                     1.7301      0.299      5.784      0.000       1.144       2.316
word_hp                       -3.6044      0.387     -9.316      0.000      -4.363      -2.846
word_hpl                      -0.1806      0.409     -0.442      0.659      -0.982       0.620
word_george                   -5.7798      0.758     -7.623      0.000      -7.266      -4.294
word_650                       2.1047      0.408      5.164      0.000       1.306       2.904
word_lab                      -0.6635      0.509     -1.303      0.193      -1.662       0.335
word_labs                     -0.1804      0.456     -0.395      0.693      -1.075       0.714
word_telnet

In [31]:
# Odds of an email being spam if it contains the word "free"
np.exp(1.5427)

4.6772016824638545

>Thus, the odds that an email is spam increase almost 5 times if that email contains the word free. On the other hand, we see next that if the email contains the word george, the odds of it being spam drop by a factor larger than 300.

Taddy, Matt. Business Data Science: Combining Machine Learning and Economics to Optimize, Automate, and Accelerate Business Decisions . McGraw-Hill Education. Kindle Edition. 

In [32]:
# Odds of an email being spam if it contains the word "George"
1/np.exp(-5.7798)

323.6944450539114

In [40]:
log_model.predict(email.iloc[[1,4000]])

1       0.999983
4000    0.000006
dtype: float64

In [36]:
email.iloc[1]

word_make                        1.000
word_address                     1.000
word_all                         1.000
word_3d                          0.000
word_our                         1.000
word_over                        1.000
word_remove                      1.000
word_internet                    1.000
word_order                       0.000
word_mail                        1.000
word_receive                     1.000
word_will                        1.000
word_people                      1.000
word_report                      1.000
word_addresses                   1.000
word_free                        1.000
word_business                    1.000
word_email                       1.000
word_you                         1.000
word_credit                      0.000
word_your                        1.000
word_font                        0.000
word_000                         1.000
word_money                       1.000
word_hp                          0.000
word_hpl                 

In [41]:
email.iloc[[1,4000]]

word_make  word_address  word_all  word_3d  word_our  word_over  \
1             1             1         1        0         1          1   
4000          0             0         0        0         0          0   

      word_remove  word_internet  word_order  word_mail  ...  char_semicolon  \
1               1              1           0          1  ...               0   
4000            0              0           0          0  ...               1   

      char_leftbrac  char_leftsquarebrac  char_exclaim  char_dollar  \
1                 1                    0             1            1   
4000              0                    1             0            0   

      char_pound  capital_run_length_average  capital_run_length_longest  \
1              1                       5.114                         101   
4000           0                       1.725                          13   

      capital_run_length_total  spam  
1                         1028     1  
4000                        69     0  

[2 rows x 58 columns]